In [1]:
#! nvidia-smi

In [2]:
#conda install pytorch torchvision -c pytorch

In [3]:
import os
def EXIT_NOTEBOOK(): os._exit(00)
#os.environ['CUDA_VISIBLE_DEVICES'] = '3'
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3' 

Changes in code cell 4. added line 3.  

In [4]:
import numpy as np
import matplotlib.pyplot as plt
plt.rcParams['text.usetex'] = False
from tqdm.notebook import tqdm
import random
import torch 
from torch import nn
import torch.nn.functional as func
import seaborn as sns
import matplotlib.ticker

# # ps
# import pysindy as ps

# sns.set_theme()
torch.set_default_dtype(torch.float64)
plt.rcParams['text.usetex'] = True

# Set the vector field

In [5]:
def get_v(x):
    x = x[...,-1]
    return np.stack([3*x*np.exp(-2*x**2),3*x*np.exp(-2*x**2)-5*x],axis=-1)

In [6]:
dim = 1

# Dataset for X

In [7]:
X = np.random.uniform(-3,3,(10000,1))
get_v(X[0]),get_v(X[:2])

(array([-1.87021141e-06,  1.38318488e+01]),
 array([[-1.87021141e-06,  1.38318488e+01],
        [ 6.20712960e-01, -5.29253718e-01]]))

# Set the NN model and Solver with training process

In [8]:
def relu2(X): return func.relu(X)**2
def tanh(X): return func.tanh(X)
class FCNN(nn.Module):
    def __init__(self,input_dim=2,output_dim=1,num_hidden=2,hidden_dim=10,act=func.tanh,transform=None):
        super().__init__()
         
        self.input_dim = input_dim
        self.output_dim = output_dim
        self.layers  = nn.ModuleList([nn.Linear(input_dim,hidden_dim)])
        for _ in range(num_hidden-1): self.layers.append(nn.Linear(hidden_dim,hidden_dim))
        self.act     = act
        self.out     = nn.Linear(hidden_dim,output_dim)
        self.transform = transform
    def forward(self,X):
        if self.transform is not None: X = self.transform(X)
        for layer in self.layers: X = self.act(layer(X))
        Y = self.out(X)
        return Y
class Model(nn.Module):
    def __init__(self,dim,model_U,unit_len=int(5e3)):
        super().__init__()
        self.dim      = dim
        self.model_U  = model_U
        self.unit_len = unit_len
        self.mu       = nn.Parameter(torch.tensor([0.]*dim),requires_grad=False) 
        self.sigma    = nn.Parameter(torch.tensor([1.]*dim),requires_grad=False)
        #above two lines should work, but if something doesn't work, check here! Does current self.mu and self.sigma code work if dim>1. Should return a vector since what we're trying to do is calculate mu
        #and sigma separately for each imnputted feature. mu is parameter[0] for each row.
        self.coef_U   = nn.Parameter(torch.tensor(1.),requires_grad=False)
        #self.mu       = nn.Parameter(torch.tensor([0.]*dim).cuda(),requires_grad=False)
        #self.sigma    = nn.Parameter(torch.tensor([1.]*dim).cuda(),requires_grad=False)
        #self.coef_U   = nn.Parameter(torch.tensor(1.).cuda(),requires_grad=False)
    def get_U_harmonic(self,X): return torch.sum(X**2,axis=-1)


    def get_U_dU(self,X): #X is all data aka all positions
        I = int(np.ceil(len(X)/self.unit_len)) #will have to change the evenness of the split eventually. this is dividing up the data
        U,dU = [],[]
        for i in range(I):
            X_sub = X[i*self.unit_len:(i+1)*self.unit_len] #**needs changing for dimensionality. 1bead to 3bead
            if not torch.is_tensor(X_sub): X_sub = torch.tensor(X_sub,requires_grad=True)#.cuda()
            X_    = (X_sub-self.mu)/self.sigma
            U_    = self.coef_U*(self.model_U(X_).view(-1) + self.get_U_harmonic(X_))
            dU_   = torch.autograd.grad(U_,X_sub,torch.ones_like(U_),create_graph=True)[0] # it is X_sub!!!
            U.append(U_)
            dU.append(dU_)
        U = torch.hstack(U) #if U is a matrix instead of a scalar, will torch.hstack(U) stack the list that is in each element in U? Or something else.
        dU = torch.vstack(dU)
        return U,dU
    
    
    def get_U_np(self,X): 
        U,_ = self.get_U_dU(X);
        return U.cpu().data.numpy()
class Solver():
    def __init__(self,model):
        self.model=model
    def train_model(self,data_train,data_test,get_loss,optimizer,
                    n_steps,batch_size,scheduler=None,n_show_loss=100,error_model=None,use_tqdm=True):
        if use_tqdm: step_range = tqdm(range(n_steps))
        else: step_range = range(n_steps)
        loss_step = []
        for i_step in step_range:
            if i_step%n_show_loss==0:
                loss_train,loss_test = get_loss(self.model,data_train)[:-1],\
                                       get_loss(self.model,data_test)[:-1]
                
                def show_num(x): 
                    if abs(x)<100 and abs(x)>.01: return '%0.5f'%x
                    else: return '%0.2e'%x
                item1 = '%2dk'%np.int_(i_step/1000)
                item2 = 'Loss: '+' '.join([show_num(k) for k in loss_train])
                item3 = ' '.join([show_num(k) for k in loss_test])
                item4 = ''
                if error_model is not None: item4 = 'E(QP): %0.4f' % (error_model(self.model))
                print(', '.join([item1,item2,item3,item4]))
                loss_step = loss_step + [i_step] + [k.cpu().data.numpy() for k in loss_train]\
                                                 + [k.cpu().data.numpy() for k in loss_train]
            data_batch = data_train[random.sample(range(len(data_train)),
                                                  min(batch_size,len(data_train)))]
#             print(i_step,data_batch.shape)
            loss = get_loss(self.model,data_batch)[-1]
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            if scheduler is not None: scheduler.step()
        if error_model is not None: 
            print("Error: %0.5f" % (error_model(self.model)))
        return loss_step

In [9]:
model_U = FCNN(input_dim=dim,output_dim=1,num_hidden=3,hidden_dim=10,act=tanh)#.cuda()
model   = Model(dim,model_U=model_U)#.cuda();
SOL     = Solver(model)

In [10]:
model.get_U_dU(X[:3])

(tensor([7.6716, 0.0294, 6.6735], grad_fn=<CatBackward0>),
 tensor([[-5.5356],
         [ 0.4380],
         [ 5.1785]], grad_fn=<CatBackward0>))

# Set the loss function and Train the model for differen a_k(x)

Changed code cell 23. added keepdim on getmean of residue

In [11]:
def plot_model(model,cmap='terrain',max_V = 10):
    
    xx     = np.linspace(0,2,1000).reshape(-1,1)
    U_NN   = model.get_U_np(xx)
    U_NN_min = U_NN.min()
    U_NN  = U_NN-U_NN_min

    fig, ax    = plt.subplots(1,1,figsize=(5,3),dpi=200,constrained_layout=True)
    c      = ax.plot(xx[:,0],U_NN,'-',lw=1.5,)

    ax.tick_params(axis="both", labelsize=10)
    plt.show()
#def get_a(X,k=choose_id):
#    if choose_id==1: return 2*torch.exp(-3*X**2)
#    if choose_id==2: return 2/(1+torch.exp(20*(torch.abs(X)-0.75)))
#    if choose_id==3: return 4/(1+torch.exp(20*(torch.abs(X)-0.75)))
def get_loss(model,data):

    X = data
    X = torch.tensor(X,requires_grad=True)#.cuda()
    _,dU = model.get_U_dU(X)

    #CTMC
    param = 3
    c = 0.5*param
    
    tmp1 = torch.detach(3*X*torch.exp(-2*X**2)) #common part of v1 and v2, aka v1
    tmp2 = torch.detach(-2*param/(1+torch.exp(20*(torch.abs(X)-0.75)))) #affinity fucntion
    #tmp2 = torch.detach(-get_a(X))
    tmp3 = torch.detach(-tmp2)
    tmp4 = torch.detach(tmp1-5*X) #v2
    Res = ( dU*(dU+tmp1)+tmp2 ) * (dU*(dU+tmp4)-c) - c*tmp3 #determinant 
    loss = torch.mean( Res**2, dim= (1), keepdim=True ) #norm of determinant -> loss function
    
    return loss#,loss

plot_model(model)
get_loss(model,X[:3])

RuntimeError: Failed to process string with tex because latex could not be found

<Figure size 1000x600 with 1 Axes>

tensor([[2.1118e+06],
        [2.2477e-01],
        [1.2675e+06]], grad_fn=<MeanBackward1>)

In [12]:
#for choose_id in [1,2,3]:
model_U = FCNN(input_dim=dim,output_dim=1,num_hidden=3,hidden_dim=10,act=tanh)#.cuda()
model   = Model(dim,model_U=model_U)#.cuda();
SOL     = Solver(model)

print(model.mu,model.sigma,model.coef_U)
    #optimizer = torch.optim.Adam(model.parameters(), lr=torch.tensor(0.001).cuda())
optimizer = torch.optim.Adam(model.parameters(), lr=torch.tensor(0.001))
scheduler = None
_loss_step = SOL.train_model(data_train=X,data_test=X,
                             get_loss=get_loss,optimizer=optimizer,scheduler=scheduler,
                             n_steps=int(5e4+1),batch_size=500,n_show_loss=1000,use_tqdm=True)
torch.cuda.empty_cache()
plot_model(model)
   # torch.save(model.state_dict(), "savee/model_"+str(choose_id))
#torch.save(model.state_dict(),"savee/model_anaconda3")

Parameter containing:
tensor([0.]) Parameter containing:
tensor([1.]) Parameter containing:
tensor(1.)


  0%|          | 0/50001 [00:00<?, ?it/s]

 0k, Loss: 2.11e+06 0.29145 1.29e+06 2.45e+02 0.52827 0.24387 38.25927 0.01321 1.31e+06 2.04e+04 0.33708 0.04895 1.68e+06 1.13e+04 3.61e+06 2.77e+05 4.47e-04 1.81e+03 2.93e+04 9.63e+04 1.61e+06 1.82e+06 2.32e+04 1.35e+06 3.19e+05 3.06e+06 1.10e+05 3.48e+03 7.65e+03 0.07416 2.93e+06 3.15e+06 3.58e+03 2.05e+06 1.29e+05 1.92e+05 2.76e+03 2.23e+04 2.81e+06 6.39e+04 1.10e+06 8.02e+05 1.61e+02 1.84e+03 5.23e+03 4.85e+03 1.91e+06 2.50e+05 4.32e+03 6.37e-05 7.22e+04 1.86e+03 2.18e+05 1.11e+05 1.28e+04 0.01336 0.85903 3.06e+05 1.04e+05 5.08e+04 5.63e+04 1.97e+04 0.35605 5.86e+03 0.23262 2.25e+06 1.67e+05 3.13e+03 0.24773 9.07e+05 0.04873 6.48e+04 6.21e+05 1.90e+04 4.88e+03 0.29145 0.58437 6.60e+05 3.52e+06 1.19e+04 1.36e+03 3.43e+04 4.06e+05 1.38e+05 7.62e-06 0.52507 5.21e+03 8.29e+04 1.01e+06 5.44e+05 1.95e+05 0.28517 1.60e+04 6.64e+02 2.24e+04 1.00e+05 0.52522 0.09251 0.72673 1.25e-03 1.18e+03 1.14198 3.05e+06 1.06932 3.91e+03 1.73e+06 5.93e+03 0.11429 0.65802 1.44e+05 1.20e+06 0.91168 0.0355

RuntimeError: Failed to process string with tex because latex could not be found

<Figure size 1000x600 with 1 Axes>

In [13]:
#torch.save(model.state_dict(), "savee/model_99")
#model.state_dict()

In [14]:
fig, ax  = plt.subplots(1,1,figsize=(4,3),dpi=200,constrained_layout=True)
xx       = np.linspace(0,2,1000).reshape(-1,1)
U_NN     = model.get_U_np(xx)
U_NN_min = U_NN.min()
U_NN     = U_NN-U_NN_min
c        = ax.plot(xx[:,0],U_NN,'-',lw=1.5)
ax.legend(fontsize=10)
ax.set_xlabel('$x$',fontsize=10)
ax.set_ylabel('$U(x)$',fontsize=10)
ax.set_xlim([0,2])
ax.set_yticks([0,0.2,0.4,0.6,0.8,1,1.2])
ax.set_xticks([0,.5,1.,1.5,2])
ax.yaxis.grid(linestyle='--')
ax.tick_params(axis="both", labelsize=10)
plt.show()

No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.


RuntimeError: Failed to process string with tex because latex could not be found

<Figure size 800x600 with 1 Axes>

In [15]:
U_NN

array([6.00002412e-03, 5.91671617e-03, 5.83398162e-03, 5.75182242e-03,
       5.67024047e-03, 5.58923766e-03, 5.50881577e-03, 5.42897658e-03,
       5.34972180e-03, 5.27105308e-03, 5.19297204e-03, 5.11548024e-03,
       5.03857918e-03, 4.96227033e-03, 4.88655509e-03, 4.81143483e-03,
       4.73691085e-03, 4.66298442e-03, 4.58965673e-03, 4.51692896e-03,
       4.44480220e-03, 4.37327751e-03, 4.30235591e-03, 4.23203835e-03,
       4.16232574e-03, 4.09321893e-03, 4.02471874e-03, 3.95682591e-03,
       3.88954116e-03, 3.82286515e-03, 3.75679848e-03, 3.69134171e-03,
       3.62649535e-03, 3.56225985e-03, 3.49863564e-03, 3.43562305e-03,
       3.37322241e-03, 3.31143397e-03, 3.25025795e-03, 3.18969451e-03,
       3.12974375e-03, 3.07040575e-03, 3.01168051e-03, 2.95356800e-03,
       2.89606814e-03, 2.83918080e-03, 2.78290579e-03, 2.72724288e-03,
       2.67219180e-03, 2.61775222e-03, 2.56392377e-03, 2.51070602e-03,
       2.45809850e-03, 2.40610069e-03, 2.35471202e-03, 2.30393189e-03,
      

In [16]:
import scipy.io as scio
from scipy.io import savemat


# Visualizing the results for different a_k(x)

In [17]:
def plot_models(models):
    
    xx       = np.linspace(0,2,1000).reshape(-1,1)
    fig, ax  = plt.subplots(1,1,figsize=(4,3),dpi=200,constrained_layout=True)
    
    for k,model_name in enumerate(models):
        model.load_state_dict(torch.load(model_name))
        U_NN     = model.get_U_np(xx)
        U_NN_min = U_NN.min()
        U_NN     = U_NN-U_NN_min
        c        = ax.plot(xx[:,0],U_NN,'-',lw=1.5,label="$a_{%d}(x)$"%(k+1))
    ax.legend(fontsize=10)
    ax.set_xlabel('$x$',fontsize=10)
    ax.set_ylabel('$U(x)$',fontsize=10)
    ax.set_xlim([0,2])
    ax.set_yticks([0,0.2,0.4,0.6,0.8,1,1.2])
    ax.set_xticks([0,.5,1.,1.5,2])
    ax.yaxis.grid(linestyle='--')
    ax.tick_params(axis="both", labelsize=10)
    plt.show()
    
plot_models(["savee/model_anaconda3"])
#plot_models(["savee/model_a1_update", "savee/model_a2_update", "savee/model_a3_update", "savee/model_a4", "savee/model_a5_update"])

/var/folders/jf/w5m4c3sj361fdh8b5wz1cy1m0000gn/T/ipykernel_57038/1776175810.py:7: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load(model_name))

FileNotFoundError: [Errno 2] No such file or directory: 'savee/model_anaconda3'

Error in callback <function _draw_all_if_interactive at 0x11fa24360> (for post_execute), with arguments args (),kwargs {}:


RuntimeError: Failed to process string with tex because latex could not be found

RuntimeError: Failed to process string with tex because latex could not be found

<Figure size 800x600 with 1 Axes>

In [ ]:
model

In [ ]:
torch.load("/Users/annacoletti/Desktop/savee/model_a3_update.mat")